In [ ]:
!pip3 install plotly folium mapclassify matplotlib

This notebook uses OSM data downloaded from here: https://overpass-turbo.eu/ using the following query:

```
[out:json];
(
  relation["boundary"="administrative"]["admin_level"="2"]["name"="Canada"];
  relation["boundary"="administrative"]["admin_level"="2"]["name"="United States"];
);
out geom;
```

The data may be used for ANY purpose under the Open Database License (ODbL) v1.0. https://www.openstreetmap.org/copyright

In [2]:
import geopandas as gpd
from shapely import Point
import time

gdf = gpd.read_file(
    "/workspaces/sailbot_workspace/src/local_pathfinding/land/territorial_waters.geojson"
)

gdf = gdf[["id", "geometry"]]
gdf = gdf.head(2)  # only the first two rows actually contain land

# The dataset is tiny, only 160 Bytes
print("Bytes: " + str(gdf.memory_usage().sum()))

print(gdf.head)

gdf.explore()

Bytes: 160
<bound method NDFrame.head of                  id                                           geometry
0   relation/148838  MULTIPOLYGON (((-131.22407 54.69433, -131.2183...
1  relation/1428125  MULTIPOLYGON (((-52.87038 49.76062, -52.87061 ...>


/home/ros/.local/lib/python3.10/site-packages/matplotlib/projections/__init__.py:63: UserWarning: Unable to import Axes3D. This may be due to multiple versions of Matplotlib being installed (e.g. as a system package and as a pip package). As a result, the 3D projection is not available.
  warnings.warn("Unable to import Axes3D. This may be due to multiple versions of "
/usr/lib/python3/dist-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.17.3 and <1.25.0 is required for this version of SciPy (detected version 1.26.4
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [3]:
from shapely.geometry import MultiPolygon

point = Point(-130.273455, 48.899258)

start = time.time()
for i in range(500):
    result = gdf.contains(point)
end = time.time()
print("GeoDataframe Time: " + str((end - start) / 500.0))

geoms = list(gdf.iloc[0]["geometry"].geoms) + list(gdf.iloc[1]["geometry"].geoms)
print(len(geoms))

multi_poly = MultiPolygon(geoms)
# repair invalid polygons
multi_poly = multi_poly.buffer(0)

start = time.time()
for i in range(500):
    result = multi_poly.contains(point)
end = time.time()
print("MultiPolygon Time: " + str((end - start) / 500.0))

GeoDataframe Time: 0.011881634712219239
58
MultiPolygon Time: 0.006774210453033448


In [4]:
multi_poly

In [5]:
import csv
from shapely.geometry import Polygon, LineString
from shapely.ops import split
from os.path import normpath

MAP_SEL_POLYGON = normpath(
    "/workspaces/sailbot_workspace/src/local_pathfinding/land/csv/map_sel.csv"
)

# Load in a custom Polygon which hugs coastline, to prune off unneeded inland polygons
with open(MAP_SEL_POLYGON, "r") as f:
    reader = csv.reader(f)
    # skip header
    reader.__next__()
    map_sel = Polygon([[float(row[1]), float(row[0])] for row in reader])

# Slice off section of map_sel west of the International Date Line
# transforming a polygon that crosses the IDL has undesired results
IDL = LineString([(-180, 90), (-180, -90)])
map_sel_east = split(map_sel, IDL).geoms[0]

# clip polygons in multi_poly to map_sel_east
multi_poly_clipped = multi_poly.intersection(map_sel_east)

In [6]:
import pyproj

WGS84 = pyproj.CRS("EPSG:4326")

# create a GeoDataFrame from the MultiPolygon
gdf_clipped = gpd.GeoDataFrame(geometry=[multi_poly_clipped], crs=WGS84)
print(gdf.head)

gdf_clipped.explore()

<bound method NDFrame.head of                  id                                           geometry
0   relation/148838  MULTIPOLYGON (((-131.22407 54.69433, -131.2183...
1  relation/1428125  MULTIPOLYGON (((-52.87038 49.76062, -52.87061 ...>


In [7]:
start = time.time()
for i in range(500):
    result = multi_poly_clipped.contains(point)
end = time.time()
print("MultiPolygonClipped Time: " + str((end - start) / 500.0))

MultiPolygonClipped Time: 0.0014614768028259277


In [8]:
# Total time to generate a Multipolygon for navigation use
def load_land():
    gdf = gpd.read_file(
        "/workspaces/sailbot_workspace/src/local_pathfinding/land/territorial_waters.geojson"
    )
    gdf = gdf[["id", "geometry"]]
    gdf = gdf.head(2)
    geoms = list(gdf.iloc[0]["geometry"].geoms) + list(gdf.iloc[1]["geometry"].geoms)
    multi_poly = MultiPolygon(geoms)
    multi_poly = multi_poly.buffer(0)
    MAP_SEL_POLYGON = normpath(
        "/workspaces/sailbot_workspace/src/local_pathfinding/land/csv/map_sel.csv"
    )
    with open(MAP_SEL_POLYGON, "r") as f:
        reader = csv.reader(f)
        reader.__next__()
        map_sel = Polygon([[float(row[1]), float(row[0])] for row in reader])
    IDL = LineString([(-180, 90), (-180, -90)])
    map_sel_east = split(map_sel, IDL).geoms[0]
    multi_poly_clipped = multi_poly.intersection(map_sel_east)


start = time.time()
for i in range(10):
    load_land()
end = time.time()
print("Land Data Init Time: " + str((end - start) / 10.0) + "Seconds")

Land Data Init Time: 0.9333342552185059Seconds


In [9]:
import pickle
import os
from typing import Any


def dump_pkl(object: Any, file_path: str):
    os.makedirs(os.path.dirname(file_path), exist_ok=True)
    with open(file_path, "wb") as f:
        pickle.dump(object, f, protocol=pickle.HIGHEST_PROTOCOL)


def load_pkl(file_path: str) -> Any:
    with open(file_path, "rb") as f:
        return pickle.load(f)

In [10]:
def pickle_land():
    gdf = gpd.read_file(
        "/workspaces/sailbot_workspace/src/local_pathfinding/land/territorial_waters.geojson"
    )
    gdf = gdf[["id", "geometry"]]
    gdf = gdf.head(2)
    geoms = list(gdf.iloc[0]["geometry"].geoms) + list(gdf.iloc[1]["geometry"].geoms)
    multi_poly = MultiPolygon(geoms)
    multi_poly = multi_poly.buffer(0)
    MAP_SEL_POLYGON = normpath(
        "/workspaces/sailbot_workspace/src/local_pathfinding/land/csv/map_sel.csv"
    )
    with open(MAP_SEL_POLYGON, "r") as f:
        reader = csv.reader(f)
        reader.__next__()
        map_sel = Polygon([[float(row[1]), float(row[0])] for row in reader])
    IDL = LineString([(-180, 90), (-180, -90)])
    map_sel_east = split(map_sel, IDL).geoms[0]
    multi_poly_clipped = multi_poly.intersection(map_sel_east)
    dump_pkl(
        multi_poly_clipped, "/workspaces/sailbot_workspace/src/local_pathfinding/land/pkl/land.pkl"
    )


pickle_land()

start = time.time()
for i in range(10):
    land = None
    land = load_pkl("/workspaces/sailbot_workspace/src/local_pathfinding/land/pkl/land.pkl")
end = time.time()
print("Land Data PKL Load Time: " + str((end - start) / 10.0) + "Seconds")

Land Data PKL Load Time: 0.0010764360427856444Seconds
